# Análisis de Esfuerzo de Compra

Exploración rápida para evaluar la asequibilidad de vivienda combinando precios de `fact_precios`, renta declarada en `fact_renta` y geometrías de `dim_barrios`. El índice utilizado aproxima cuántas rentas anuales (hogar promedio) se requieren para adquirir una vivienda tipo de 70 m².



In [1]:
from __future__ import annotations

import json
from pathlib import Path

import pandas as pd
import plotly.express as px
import sqlite3

DB_PATH = Path("../data/processed/database.db").resolve()



In [2]:
def load_data(target_year: int = 2022) -> pd.DataFrame:
    """Carga precios, renta y geometría para el año objetivo."""
    if not DB_PATH.exists():
        raise FileNotFoundError(f"No se encuentra la base de datos en {DB_PATH}")

    conn = sqlite3.connect(DB_PATH)
    try:
        precios = pd.read_sql(
            """
            SELECT barrio_id, AVG(precio_m2_venta) AS avg_precio_m2
            FROM fact_precios
            WHERE anio = ? AND precio_m2_venta IS NOT NULL
            GROUP BY barrio_id
            """,
            conn,
            params=(target_year,),
        )

        renta = pd.read_sql(
            """
            SELECT barrio_id, renta_euros
            FROM fact_renta
            WHERE anio = ?
            """,
            conn,
            params=(target_year,),
        )

        barrios = pd.read_sql(
            """
            SELECT barrio_id, barrio_nombre, barrio_nombre_normalizado,
                   distrito_nombre, geometry_json
            FROM dim_barrios
            WHERE geometry_json IS NOT NULL
            """,
            conn,
        )
    finally:
        conn.close()

    df = (
        barrios
        .merge(precios, on="barrio_id", how="left")
        .merge(renta, on="barrio_id", how="left")
    )

    df["precio_estimado_vivienda"] = df["avg_precio_m2"] * 70  # vivienda tipo 70 m²
    df["effort_ratio"] = df["precio_estimado_vivienda"] / df["renta_euros"]

    return df.dropna(subset=["avg_precio_m2", "renta_euros"]).copy()


data_2022 = load_data(2022)
data_2022.head()



barrio_id                          barrio_nombre  \
0          1                               el Raval   
1          2                         el Barri Gòtic   
2          3                         la Barceloneta   
3          4  Sant Pere, Santa Caterina i la Ribera   
4          5                          el Fort Pienc   

        barrio_nombre_normalizado distrito_nombre  \
0                         elraval    Ciutat Vella   
1                    elbarrigotic    Ciutat Vella   
2                   labarceloneta    Ciutat Vella   
3  santperesantacaterinailaribera    Ciutat Vella   
4                     elfortpienc        Eixample   

                                       geometry_json  avg_precio_m2  \
0  {"type": "Polygon", "coordinates": [[[2.164713...        3202.97   
1  {"type": "Polygon", "coordinates": [[[2.177014...        4755.71   
2  {"type": "Polygon", "coordinates": [[[2.196228...        4656.68   
3  {"type": "Polygon", "coordinates": [[[2.183451...        4739.02   
4  {"type": "Polygon", "coordinates": [[[2.183527...        4296.04   

    renta_euros  precio_estimado_vivienda  effort_ratio  
0  14221.142857                  224207.9     15.765814  
1  18668.111111                  332899.7     17.832533  
2  17965.909091                  325967.6     18.143674  
3  19655.153846                  331731.4     16.877578  
4  24163.200000                  300722.8     12.445487

**Nota metodológica**

- Año de referencia: 2022 (último año disponible con renta media).
- `avg_precio_m2`: media de precio de venta m² (Portal de Dades + otras fuentes).
- `renta_euros`: renta media anual del barrio.
- `effort_ratio`: nº de rentas anuales necesarias para comprar 70 m². Valores altos implican menor asequibilidad.



In [3]:
def build_geojson(df: pd.DataFrame) -> dict:
    features = []
    for _, row in df.iterrows():
        geometry = json.loads(row["geometry_json"])
        features.append(
            {
                "type": "Feature",
                "geometry": geometry,
                "properties": {
                    "barrio_id": int(row["barrio_id"]),
                    "barrio_nombre": row["barrio_nombre"],
                    "distrito_nombre": row["distrito_nombre"],
                },
            }
        )
    return {"type": "FeatureCollection", "features": features}


affordability_df = data_2022.copy()
affordability_geojson = build_geojson(affordability_df)

fig = px.choropleth(
    affordability_df,
    geojson=affordability_geojson,
    locations="barrio_id",
    featureidkey="properties.barrio_id",
    color="effort_ratio",
    color_continuous_scale="Inferno",
    hover_data={
        "barrio_nombre": True,
        "distrito_nombre": True,
        "avg_precio_m2": ":.0f",
        "renta_euros": ":.0f",
        "effort_ratio": ":.2f",
    },
    labels={"effort_ratio": "Rentas anuales (70 m²)"},
    title="Índice de esfuerzo de compra (2022)",
)
fig.update_geos(fitbounds="locations", visible=False)
fig.update_layout(margin=dict(r=0, t=60, l=0, b=0))
fig.show()



In [4]:
output_file = Path("map_affordability.html")
fig.write_html(output_file)
print(f"Mapa exportado a {output_file.resolve()}")



Mapa exportado a /Users/adrianiraeguialvear/Projects/barcelona-housing-demographics-analyzer/notebooks/map_affordability.html


## Análisis de Correlaciones

¿Qué variable explica mejor el precio de la vivienda: la renta media del barrio o la densidad de población?



In [5]:
import numpy as np
import plotly.graph_objects as go

def load_correlation_data(year: int = 2022) -> pd.DataFrame:
    """Carga precio, renta y densidad para el año objetivo."""
    conn = sqlite3.connect(DB_PATH)
    try:
        query = """
        SELECT
            b.barrio_id,
            b.barrio_nombre,
            b.distrito_nombre,
            p.avg_precio_m2,
            r.renta_euros,
            d.densidad_hab_km2,
            d.poblacion_total
        FROM dim_barrios b
        LEFT JOIN (
            SELECT barrio_id, AVG(precio_m2_venta) AS avg_precio_m2
            FROM fact_precios
            WHERE anio = ? AND precio_m2_venta IS NOT NULL
            GROUP BY barrio_id
        ) p ON b.barrio_id = p.barrio_id
        LEFT JOIN (
            SELECT barrio_id, renta_euros
            FROM fact_renta WHERE anio = ?
        ) r ON b.barrio_id = r.barrio_id
        LEFT JOIN (
            SELECT barrio_id, densidad_hab_km2, poblacion_total
            FROM fact_demografia WHERE anio = ?
        ) d ON b.barrio_id = d.barrio_id
        """
        df = pd.read_sql(query, conn, params=(year, year, year))
    finally:
        conn.close()
    return df.dropna()


corr_df = load_correlation_data(2022)

# Calcular matriz de correlación
corr_cols = ["avg_precio_m2", "renta_euros", "densidad_hab_km2", "poblacion_total"]
corr_matrix = corr_df[corr_cols].corr()

labels = ["Precio €/m²", "Renta anual", "Densidad hab/km²", "Población total"]

fig_corr = go.Figure(
    data=go.Heatmap(
        z=corr_matrix.values,
        x=labels,
        y=labels,
        colorscale="RdBu_r",
        zmin=-1,
        zmax=1,
        text=np.round(corr_matrix.values, 2),
        texttemplate="%{text}",
        textfont={"size": 14},
        hovertemplate="Correlación %{y} vs %{x}: %{z:.2f}<extra></extra>",
    )
)
fig_corr.update_layout(
    title="Matriz de Correlación (2022)",
    width=600,
    height=500,
)
fig_corr.show()



In [6]:
# Scatter plots: Precio vs Renta y Precio vs Densidad
from plotly.subplots import make_subplots

fig_scatter = make_subplots(
    rows=1, cols=2,
    subplot_titles=("Precio vs Renta", "Precio vs Densidad"),
    horizontal_spacing=0.1,
)

# Precio vs Renta
fig_scatter.add_trace(
    go.Scatter(
        x=corr_df["renta_euros"],
        y=corr_df["avg_precio_m2"],
        mode="markers",
        marker=dict(size=10, color=corr_df["avg_precio_m2"], colorscale="Plasma"),
        text=corr_df["barrio_nombre"],
        hovertemplate="<b>%{text}</b><br>Renta: €%{x:,.0f}<br>Precio: €%{y:,.0f}/m²<extra></extra>",
    ),
    row=1, col=1,
)

# Precio vs Densidad
fig_scatter.add_trace(
    go.Scatter(
        x=corr_df["densidad_hab_km2"],
        y=corr_df["avg_precio_m2"],
        mode="markers",
        marker=dict(size=10, color=corr_df["avg_precio_m2"], colorscale="Plasma"),
        text=corr_df["barrio_nombre"],
        hovertemplate="<b>%{text}</b><br>Densidad: %{x:,.0f} hab/km²<br>Precio: €%{y:,.0f}/m²<extra></extra>",
    ),
    row=1, col=2,
)

fig_scatter.update_xaxes(title_text="Renta anual (€)", row=1, col=1)
fig_scatter.update_xaxes(title_text="Densidad (hab/km²)", row=1, col=2)
fig_scatter.update_yaxes(title_text="Precio (€/m²)", row=1, col=1)
fig_scatter.update_yaxes(title_text="Precio (€/m²)", row=1, col=2)

fig_scatter.update_layout(
    title="Relación entre Precio de Vivienda, Renta y Densidad (2022)",
    showlegend=False,
    height=450,
    width=950,
)
fig_scatter.show()

# Imprimir correlaciones
print("Correlaciones con Precio €/m²:")
print(f"  · Renta anual:      r = {corr_matrix.loc['avg_precio_m2', 'renta_euros']:.3f}")
print(f"  · Densidad hab/km²: r = {corr_matrix.loc['avg_precio_m2', 'densidad_hab_km2']:.3f}")



Correlaciones con Precio €/m²:
  · Renta anual:      r = 0.828
  · Densidad hab/km²: r = 0.059


## Detección de Gentrificación (2015 → 2022)

Identificamos los barrios donde el precio de vivienda ha subido más que la renta media, lo que indica un "esfuerzo de compra creciente" y potencial desplazamiento de residentes.



In [7]:
def load_temporal_comparison(year_start: int = 2015, year_end: int = 2022) -> pd.DataFrame:
    """
    Carga datos de precio para dos años y renta actual (2022).
    
    Nota: fact_renta solo tiene datos de 2022, así que usamos esa renta
    como referencia para calcular esfuerzo de compra en ambos periodos.
    """
    conn = sqlite3.connect(DB_PATH)
    try:
        query = """
        WITH precios_start AS (
            SELECT barrio_id, AVG(precio_m2_venta) AS precio_start
            FROM fact_precios
            WHERE anio = ? AND precio_m2_venta IS NOT NULL
            GROUP BY barrio_id
        ),
        precios_end AS (
            SELECT barrio_id, AVG(precio_m2_venta) AS precio_end
            FROM fact_precios
            WHERE anio = ? AND precio_m2_venta IS NOT NULL
            GROUP BY barrio_id
        ),
        renta_actual AS (
            SELECT barrio_id, renta_euros
            FROM fact_renta WHERE anio = 2022
        )
        SELECT
            b.barrio_id,
            b.barrio_nombre,
            b.distrito_nombre,
            b.geometry_json,
            ps.precio_start,
            pe.precio_end,
            r.renta_euros
        FROM dim_barrios b
        LEFT JOIN precios_start ps ON b.barrio_id = ps.barrio_id
        LEFT JOIN precios_end pe ON b.barrio_id = pe.barrio_id
        LEFT JOIN renta_actual r ON b.barrio_id = r.barrio_id
        WHERE b.geometry_json IS NOT NULL
        """
        df = pd.read_sql(query, conn, params=(year_start, year_end))
    finally:
        conn.close()

    # Calcular variación porcentual de precios
    df["var_precio_pct"] = ((df["precio_end"] - df["precio_start"]) / df["precio_start"]) * 100

    # Esfuerzo de compra (70 m²) usando renta actual como referencia
    # Esto nos dice: "con la renta actual, cuánto costaba comprar en 2015 vs 2022"
    df["effort_2015"] = (df["precio_start"] * 70) / df["renta_euros"]
    df["effort_2022"] = (df["precio_end"] * 70) / df["renta_euros"]
    df["effort_change"] = df["effort_2022"] - df["effort_2015"]

    # Calcular media de variación de precios de la ciudad para comparar
    city_avg_var = df["var_precio_pct"].mean()
    df["vs_city_avg"] = df["var_precio_pct"] - city_avg_var

    return df.dropna(subset=["var_precio_pct", "renta_euros"])


gentrification_df = load_temporal_comparison(2015, 2022)
print(f"Barrios analizados: {len(gentrification_df)}")
print(f"Variación media de precio en Barcelona: {gentrification_df['var_precio_pct'].mean():.1f}%")
gentrification_df[["barrio_nombre", "precio_start", "precio_end", "var_precio_pct", "effort_change"]].sort_values("var_precio_pct", ascending=False).head(10)



Barrios analizados: 73
Variación media de precio en Barcelona: 41.0%


barrio_nombre  precio_start  precio_end  \
53                             Torre Baró    639.250000     1664.47   
64                                el Clot   2505.000000     5282.14   
40                       la Vall d'Hebron   2214.290000     4642.35   
61               el Congrés i els Indians   2216.000000     4468.09   
11             la Marina del Prat Vermell   1436.333333     2825.19   
37                           la Teixonera   1870.000000     3528.24   
21  Vallvidrera, el Tibidabo i les Planes   2070.550000     3746.97   
65      el Parc i la Llacuna del Poblenou   2956.000000     5281.32   
46                            Can Peguera   1385.460000     2448.28   
39                                Montbau   1695.270000     2912.17   

    var_precio_pct  effort_change  
53      160.378569       5.598362  
64      110.863872       8.822107  
40      109.654110       7.265601  
61      101.628610       7.561820  
11       96.694593       6.070557  
37       88.675936       6.506091  
21       80.964961       3.965221  
65       78.664411       6.902140  
46       76.712428       5.102002  
39       71.782076       4.051510

In [8]:
# Mapa de Variación de Precios (proxy de presión inmobiliaria)
gentrification_geojson = build_geojson(gentrification_df)

# Usamos vs_city_avg para mostrar qué barrios subieron más que la media
fig_gent = px.choropleth(
    gentrification_df,
    geojson=gentrification_geojson,
    locations="barrio_id",
    featureidkey="properties.barrio_id",
    color="var_precio_pct",
    color_continuous_scale="RdYlGn_r",  # Rojo = mayor subida
    hover_data={
        "barrio_nombre": True,
        "distrito_nombre": True,
        "precio_start": ":.0f",
        "precio_end": ":.0f",
        "var_precio_pct": ":.1f",
        "effort_change": ":.1f",
    },
    labels={
        "var_precio_pct": "Δ Precio %",
        "precio_start": "Precio 2015 €/m²",
        "precio_end": "Precio 2022 €/m²",
        "effort_change": "Δ Esfuerzo (rentas)",
    },
    title="Variación de Precios de Vivienda (2015 → 2022)<br><sup>Rojo = mayor incremento | Verde = menor incremento</sup>",
)
fig_gent.update_geos(fitbounds="locations", visible=False)
fig_gent.update_layout(margin=dict(r=0, t=80, l=0, b=0))
fig_gent.show()



In [9]:
# Ranking: Top 10 barrios con mayor y menor incremento de precios
top_increase = gentrification_df.nlargest(10, "var_precio_pct")[
    ["barrio_nombre", "distrito_nombre", "precio_start", "precio_end", "var_precio_pct", "effort_change"]
].reset_index(drop=True)

bottom_increase = gentrification_df.nsmallest(10, "var_precio_pct")[
    ["barrio_nombre", "distrito_nombre", "precio_start", "precio_end", "var_precio_pct", "effort_change"]
].reset_index(drop=True)

city_avg = gentrification_df["var_precio_pct"].mean()
print(f"📊 MEDIA BARCELONA: {city_avg:+.1f}%\n")

print("🔴 TOP 10 BARRIOS CON MAYOR INCREMENTO DE PRECIOS (2015 → 2022)")
print("=" * 95)
print(f"{'#':>2}  {'Barrio':35} {'2015 €/m²':>10} {'2022 €/m²':>10} {'Δ Precio':>10} {'Δ Esfuerzo':>12}")
print("-" * 95)
for i, row in top_increase.iterrows():
    print(f"{i+1:2}. {row['barrio_nombre']:35} {row['precio_start']:>10,.0f} {row['precio_end']:>10,.0f} {row['var_precio_pct']:>+9.1f}% {row['effort_change']:>+11.1f}")

print(f"\n🟢 TOP 10 BARRIOS CON MENOR INCREMENTO DE PRECIOS (2015 → 2022)")
print("=" * 95)
print(f"{'#':>2}  {'Barrio':35} {'2015 €/m²':>10} {'2022 €/m²':>10} {'Δ Precio':>10} {'Δ Esfuerzo':>12}")
print("-" * 95)
for i, row in bottom_increase.iterrows():
    print(f"{i+1:2}. {row['barrio_nombre']:35} {row['precio_start']:>10,.0f} {row['precio_end']:>10,.0f} {row['var_precio_pct']:>+9.1f}% {row['effort_change']:>+11.1f}")



📊 MEDIA BARCELONA: +41.0%

🔴 TOP 10 BARRIOS CON MAYOR INCREMENTO DE PRECIOS (2015 → 2022)
 #  Barrio                               2015 €/m²  2022 €/m²   Δ Precio   Δ Esfuerzo
-----------------------------------------------------------------------------------------------
 1. Torre Baró                                 639      1,664    +160.4%        +5.6
 2. el Clot                                  2,505      5,282    +110.9%        +8.8
 3. la Vall d'Hebron                         2,214      4,642    +109.7%        +7.3
 4. el Congrés i els Indians                 2,216      4,468    +101.6%        +7.6
 5. la Marina del Prat Vermell               1,436      2,825     +96.7%        +6.1
 6. la Teixonera                             1,870      3,528     +88.7%        +6.5
 7. Vallvidrera, el Tibidabo i les Planes      2,071      3,747     +81.0%        +4.0
 8. el Parc i la Llacuna del Poblenou        2,956      5,281     +78.7%        +6.9
 9. Can Peguera                              1

## Resumen de Hallazgos

### Correlaciones (2022)
- El **precio de vivienda** tiene mayor correlación con la **renta media** del barrio que con la densidad de población.
- Los barrios con mayores ingresos tienden a tener precios de vivienda más altos (relación positiva esperada).
- La densidad poblacional tiene una correlación más débil o incluso negativa con el precio.

### Presión Inmobiliaria (2015 → 2022)
- **Nota metodológica**: Solo tenemos datos de renta para 2022, por lo que analizamos la variación de precios como proxy de presión inmobiliaria.
- **Δ Esfuerzo de compra**: Calculado usando la renta actual (2022) como referencia para ambos periodos. Muestra cuántas rentas anuales adicionales se necesitan ahora vs. 2015 para comprar 70 m².
- Los barrios con **mayor incremento de precios** (rojos en el mapa) son candidatos a estudios más profundos de gentrificación.
- Los barrios con **menor incremento** (verdes) pueden indicar:
  - Zonas ya consolidadas con precios altos estables.
  - Zonas periféricas con menor demanda.
  - Zonas con políticas de vivienda social efectivas.



In [10]:
# Exportar figuras adicionales
fig_corr.write_html("map_correlation_matrix.html")
fig_scatter.write_html("scatter_precio_renta_densidad.html")
fig_gent.write_html("map_gentrification.html")

print("Archivos exportados:")
print("  - map_affordability.html (esfuerzo de compra 2022)")
print("  - map_correlation_matrix.html (matriz de correlación)")
print("  - scatter_precio_renta_densidad.html (scatter plots)")
print("  - map_gentrification.html (índice de gentrificación 2015-2022)")



Archivos exportados:
  - map_affordability.html (esfuerzo de compra 2022)
  - map_correlation_matrix.html (matriz de correlación)
  - scatter_precio_renta_densidad.html (scatter plots)
  - map_gentrification.html (índice de gentrificación 2015-2022)
